In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
from scipy.sparse import coo_matrix, csc_matrix, csr_matrix
from functools import reduce # Python3

In [2]:
rating = pd.read_csv('archive/rating.csv')
rating['timestamp'] = pd.to_datetime(rating.timestamp)

movie = pd.read_csv('archive/movie.csv')

genome_scores = pd.read_csv('archive/genome_scores.csv')

genome_tags = pd.read_csv('archive/genome_tags.csv')

tag = pd.read_csv('archive/tag.csv')

In [3]:
# genome_scores = genome_scores.merge(genome_tags, on='tagId', how='inner')

In [4]:
# tag = tag.merge(genome_scores, on='tag', how='inner')

In [5]:
# Средняя оценка, которую ставит пользователь + число просмотренных фильмов
user_info = rating.groupby('userId', as_index=False).agg({'rating': 'mean', 'movieId' : 'count'}) \
.rename({'rating': 'user_avg_rating', 'movieId': 'user_views_cnt'}, axis=1)
# .movieId.max()

In [6]:
# уберем из рассмотрения фильмы с маленьким количеством просмотров
def check_in_list(x):
    return [1 if genre in x else 0 for  genre in unique_genres]

movie['year'] = movie.title.str.extract('(\d\d\d\d)')
movie['title'] = movie.title.str.replace('(\(\d\d\d\d\))', '')
movie.genres = movie.genres.map(lambda x: x.split('|'))

unique_genres = list(np.unique(reduce(lambda x, y : x + y, movie.genres.to_list())))
unique_genres.remove('(no genres listed)')

movie.genres = movie.genres.apply(check_in_list)
genres = pd.DataFrame(movie.genres.to_list(), columns=unique_genres)
movie = pd.concat([movie, genres], sort=False, axis=1)
movie = movie[['movieId', 'title', 'year'] + unique_genres]
# Средняя оценка фильма + количество оценок
movie_info = rating.groupby('movieId', as_index=False) \
.agg({'rating': 'mean', 'userId': 'count'}) \
.rename({'rating': 'movie_mean_rating', 'userId': 'views_cnt'}, axis=1)

all_movies = movie.merge(movie_info, how='left', on='movieId')
all_movies.fillna(0, inplace=True)
p_90 = np.percentile(all_movies.views_cnt, 90)
popular_movie = all_movies[all_movies.views_cnt >= p_90]

In [7]:
data = rating.merge(popular_movie, how='inner', on='movieId') 

In [8]:
data = data.merge(user_info, on='userId', how='inner')

In [9]:
data.head()

userId  movieId  rating           timestamp  \
0       1        2     3.5 2005-04-02 23:53:47   
1       1       29     3.5 2005-04-02 23:31:16   
2       1       32     3.5 2005-04-02 23:33:39   
3       1       47     3.5 2005-04-02 23:32:07   
4       1       50     3.5 2005-04-02 23:29:40   

                                               title  year  Action  Adventure  \
0                                           Jumanji   1995       0          1   
1  City of Lost Children, The (Cité des enfants p...  1995       0          1   
2                Twelve Monkeys (a.k.a. 12 Monkeys)   1995       0          0   
3                              Seven (a.k.a. Se7en)   1995       0          0   
4                               Usual Suspects, The   1995       0          0   

   Animation  Children  ...  Mystery  Romance  Sci-Fi  Thriller  War  Western  \
0          0         1  ...        0        0       0         0    0        0   
1          0         0  ...        1        0       1         0    0        0   
2          0         0  ...        1        0       1         1    0        0   
3          0         0  ...        1        0       0         1    0        0   
4          0         0  ...        1        0       0         1    0        0   

   movie_mean_rating  views_cnt  user_avg_rating  user_views_cnt  
0           3.211977    22243.0         3.742857             175  
1           3.952230     8520.0         3.742857             175  
2           3.898055    44980.0         3.742857             175  
3           4.053493    43249.0         3.742857             175  
4           4.334372    47006.0         3.742857             175  

[5 rows x 29 columns]

In [10]:
user_info = data[['userId', 'movieId', 'year', 'user_avg_rating', 'user_views_cnt'] + unique_genres]

In [11]:
user_info.columns

Index(['userId', 'movieId', 'year', 'user_avg_rating', 'user_views_cnt',
       'Action', 'Adventure', 'Animation', 'Children', 'Comedy', 'Crime',
       'Documentary', 'Drama', 'Fantasy', 'Film-Noir', 'Horror', 'IMAX',
       'Musical', 'Mystery', 'Romance', 'Sci-Fi', 'Thriller', 'War',
       'Western'],
      dtype='object')

In [12]:
user_genre_weigth = user_info.groupby('userId', as_index=False).agg({genre:'mean' for genre in unique_genres})

In [13]:
# tag.groupby('userId').agg({'tag':'count'})

In [14]:
# genome_scores.sort_values(['movieId','relevance'], ascending=[True, False], inplace=True)
# genome_scores['in_group_id'] = genome_scores.groupby('movieId').cumcount() + 1

# Самые релевантные теги фильмов
# genome_scores = genome_scores[genome_scores.in_group_id <= 10]

In [15]:
genome_scores = genome_scores.merge(popular_movie, on='movieId', how='inner')
movie_tag = genome_scores.pivot_table(index=['movieId'], columns=['tagId'], values='relevance')
movie_tag.fillna(0, inplace=True)

In [16]:
movie_tag

tagId       1        2        3        4        5        6        7     \
movieId                                                                  
1        0.02500  0.02500  0.05775  0.09675  0.14675  0.21700  0.06700   
2        0.03975  0.04375  0.03775  0.04800  0.11025  0.07250  0.04775   
3        0.04350  0.05475  0.02800  0.07700  0.05400  0.06850  0.05600   
4        0.03725  0.03950  0.03675  0.03100  0.06825  0.04050  0.02325   
5        0.04200  0.05275  0.05925  0.03675  0.07525  0.12525  0.02850   
...          ...      ...      ...      ...      ...      ...      ...   
109487   0.02475  0.02325  0.05350  0.09100  0.10525  0.33325  0.08925   
111362   0.03025  0.03075  0.02900  0.06075  0.09175  0.06750  0.14525   
111759   0.02800  0.02850  0.03275  0.09750  0.08925  0.23025  0.06650   
112556   0.04200  0.02550  0.08025  0.11375  0.14800  0.13425  0.06300   
112852   0.03550  0.03425  0.01675  0.05075  0.09825  0.10550  0.04650   

tagId       8        9        10    ...     1119     1120     1121     1122  \
movieId                             ...                                       
1        0.26275  0.26200  0.03200  ...  0.03950  0.01800  0.04575  0.03275   
2        0.10975  0.09925  0.02050  ...  0.04175  0.01925  0.01725  0.02425   
3        0.18500  0.04925  0.02675  ...  0.04150  0.02675  0.02775  0.03425   
4        0.08700  0.05125  0.03025  ...  0.05750  0.03375  0.02275  0.03975   
5        0.08500  0.02950  0.02875  ...  0.04250  0.02825  0.02150  0.02600   
...          ...      ...      ...  ...      ...      ...      ...      ...   
109487   0.27625  0.07725  0.13350  ...  0.05250  0.02350  0.04200  0.03050   
111362   0.33275  0.04675  0.07875  ...  0.03400  0.03525  0.02350  0.04075   
111759   0.21100  0.08200  0.10475  ...  0.04300  0.14575  0.10600  0.02800   
112556   0.19675  0.12125  0.14575  ...  0.12900  0.02200  0.02000  0.04950   
112852   0.38075  0.22550  0.04250  ...  0.03575  0.01825  0.03750  0.03075   

tagId       1123     1124     1125     1126     1127     1128  
movieId                                                        
1        0.12500  0.04150  0.01925  0.03625  0.07775  0.02300  
2        0.12550  0.02250  0.01550  0.01475  0.09025  0.01875  
3        0.15550  0.03675  0.01700  0.01950  0.09700  0.01850  
4        0.18525  0.05925  0.01500  0.01525  0.06450  0.01300  
5        0.14275  0.02075  0.01650  0.01675  0.10750  0.01825  
...          ...      ...      ...      ...      ...      ...  
109487   0.18375  0.12625  0.04725  0.04200  0.07175  0.02400  
111362   0.33775  0.16225  0.03100  0.02300  0.09575  0.02050  
111759   0.17725  0.10250  0.05375  0.11725  0.09325  0.02975  
112556   0.37225  0.26625  0.02675  0.01925  0.05325  0.02125  
112852   0.23375  0.15575  0.03300  0.02225  0.13275  0.03350  

[2726 rows x 1128 columns]

In [17]:
# Делим данные на обучение и валидацию
temp = data.groupby('userId', as_index=False).agg({'movieId': 'count'})\
                                             .rename({'movieId': 'user_mark_cnt'}, axis=1)

temp['split_id'] = temp.user_mark_cnt * 0.25
temp['median_cnt'] = temp.user_mark_cnt.median()
temp = temp.astype({'split_id': int, 'median_cnt': int})
temp['val_cnt'] = temp[['split_id','median_cnt']].min(axis=1)
temp['train_cnt'] = temp.user_mark_cnt - temp.val_cnt

data.sort_values(['userId','timestamp'], ascending=[True, True], inplace=True)
data['in_group_id'] = data.groupby('userId').cumcount()+1   

data = data.merge(temp, how='inner', on='userId')
data['label'] = np.where(data.in_group_id <= data.train_cnt,'train', 'val')
split_timestamp = data[data.in_group_id == data.user_mark_cnt]
split_timestamp = split_timestamp[['userId', 'timestamp']]
data = data.merge(split_timestamp, on='userId', how='inner')

In [18]:
data.head()

userId  movieId  rating         timestamp_x  \
0       1      924     3.5 2004-09-10 03:06:38   
1       1      919     3.5 2004-09-10 03:07:01   
2       1     2683     3.5 2004-09-10 03:07:30   
3       1     1584     3.5 2004-09-10 03:07:36   
4       1     1079     4.0 2004-09-10 03:07:45   

                                    title  year  Action  Adventure  Animation  \
0                  2001: A Space Odyssey   2001       0          1          0   
1                      Wizard of Oz, The   1939       0          1          0   
2  Austin Powers: The Spy Who Shagged Me   1999       1          1          0   
3                                Contact   1997       0          0          0   
4                   Fish Called Wanda, A   1988       0          0          0   

   Children  ...  user_avg_rating  user_views_cnt  in_group_id  user_mark_cnt  \
0         0  ...         3.742857             175            1            155   
1         1  ...         3.742857             175            2            155   
2         0  ...         3.742857             175            3            155   
3         0  ...         3.742857             175            4            155   
4         0  ...         3.742857             175            5            155   

   split_id  median_cnt  val_cnt  train_cnt  label         timestamp_y  
0        38          63       38        117  train 2005-04-02 23:56:32  
1        38          63       38        117  train 2005-04-02 23:56:32  
2        38          63       38        117  train 2005-04-02 23:56:32  
3        38          63       38        117  train 2005-04-02 23:56:32  
4        38          63       38        117  train 2005-04-02 23:56:32  

[5 rows x 37 columns]

In [19]:
train = data[data.label == 'train']
val = data[data.label == 'val'] 

In [20]:
# Строим user-item татрицу  
user_item = train.pivot_table(index=['userId'], columns=['movieId'], values='rating')
user_item = user_item.fillna(0)
user_item = csr_matrix(user_item.values)

In [21]:
user_item

<138493x2729 sparse matrix of type '<class 'numpy.float64'>'
	with 13981486 stored elements in Compressed Sparse Row format>

In [22]:
# Cформинуем features для пользователей
d1 = {genre:'mean' for genre in unique_genres}
d2 = {'rating': 'mean'}
transform = {**d1, **d2}
user_features = train.groupby('userId', as_index=False).agg(transform)

In [23]:
user_features

userId    Action  Adventure  Animation  Children    Comedy     Crime  \
0            1  0.376068   0.299145   0.042735  0.051282  0.205128  0.162393   
1            2  0.384615   0.230769   0.025641  0.025641  0.205128  0.025641   
2            3  0.242647   0.227941   0.029412  0.044118  0.330882  0.132353   
3            4  0.476190   0.238095   0.047619  0.095238  0.476190  0.190476   
4            5  0.240000   0.280000   0.100000  0.140000  0.380000  0.120000   
...        ...       ...        ...        ...       ...       ...       ...   
138488  138489  0.241379   0.206897   0.000000  0.034483  0.241379  0.241379   
138489  138490  0.022989   0.034483   0.000000  0.022989  0.183908  0.183908   
138490  138491  0.176471   0.352941   0.176471  0.235294  0.470588  0.000000   
138491  138492  0.250000   0.266667   0.050000  0.033333  0.583333  0.183333   
138492  138493  0.264228   0.280488   0.170732  0.199187  0.410569  0.113821   

        Documentary     Drama   Fantasy  ...    Horror      IMAX   Musical  \
0          0.000000  0.324786  0.179487  ...  0.299145  0.017094  0.008547   
1          0.000000  0.384615  0.025641  ...  0.205128  0.025641  0.025641   
2          0.000000  0.404412  0.132353  ...  0.147059  0.000000  0.036765   
3          0.000000  0.238095  0.095238  ...  0.000000  0.000000  0.047619   
4          0.000000  0.460000  0.140000  ...  0.020000  0.060000  0.100000   
...             ...       ...       ...  ...       ...       ...       ...   
138488     0.000000  0.517241  0.172414  ...  0.034483  0.034483  0.000000   
138489     0.000000  0.954023  0.022989  ...  0.011494  0.000000  0.034483   
138490     0.000000  0.176471  0.117647  ...  0.235294  0.000000  0.058824   
138491     0.100000  0.300000  0.150000  ...  0.000000  0.000000  0.033333   
138492     0.004065  0.455285  0.178862  ...  0.081301  0.032520  0.105691   

         Mystery   Romance    Sci-Fi  Thriller       War   Western    rating  
0       0.145299  0.051282  0.213675  0.316239  0.059829  0.034188  3.739316  
1       0.102564  0.153846  0.282051  0.333333  0.102564  0.051282  4.102564  
2       0.058824  0.110294  0.330882  0.272059  0.044118  0.014706  4.279412  
3       0.095238  0.190476  0.190476  0.476190  0.047619  0.047619  3.523810  
4       0.040000  0.260000  0.140000  0.280000  0.020000  0.040000  4.160000  
...          ...       ...       ...       ...       ...       ...       ...  
138488  0.137931  0.137931  0.103448  0.275862  0.000000  0.034483  3.931034  
138489  0.126437  0.206897  0.034483  0.183908  0.034483  0.011494  3.643678  
138490  0.000000  0.058824  0.235294  0.176471  0.000000  0.000000  2.647059  
138491  0.033333  0.283333  0.083333  0.116667  0.016667  0.066667  4.183333  
138492  0.093496  0.211382  0.150407  0.252033  0.040650  0.016260  4.252033  

[138493 rows x 21 columns]

In [24]:
# Cформинуем features для фильмов
movie_features = train.groupby('movieId', as_index=False)\
.agg({'rating':'mean', 'userId':'count'})\
.rename({'rating':'movie_avg_rating', 'userId':'views_cnt'}, axis=1)

In [25]:
movie_features 

movieId  movie_avg_rating  views_cnt
0           1          3.919903      43154
1           2          3.194690      17854
2           3          3.126440      10507
3           4          2.853921       1862
4           5          3.051765      10142
...       ...               ...        ...
2724   109487          4.054601        815
2725   111362          3.857659        692
2726   111759          3.815296        693
2727   112556          3.950845        651
2728   112852          3.883603        988

[2729 rows x 3 columns]

In [ ]:
# Добавим к user_features и movie_features информацию о ревевантных тегах

In [38]:
movie_tag = movie_tag.reset_index()

In [39]:
movie_features = movie_features.merge(movie_tag, on='movieId', how='left')
movie_features.fillna(0, inplace=True)

In [26]:
movie_features

movieId  movie_avg_rating  views_cnt
0           1          3.919903      43154
1           2          3.194690      17854
2           3          3.126440      10507
3           4          2.853921       1862
4           5          3.051765      10142
...       ...               ...        ...
2724   109487          4.054601        815
2725   111362          3.857659        692
2726   111759          3.815296        693
2727   112556          3.950845        651
2728   112852          3.883603        988

[2729 rows x 3 columns]

In [41]:
tag = split_timestamp.merge(tag, how='inner', on='userId')
tag['timestamp_x'] = pd.to_datetime(tag.timestamp_x)
tag['timestamp_y'] = pd.to_datetime(tag.timestamp_y)

In [42]:
# tag = pd.read_csv('archive/tag.csv')

In [43]:
user_tag = tag[tag.timestamp_x <= tag.timestamp_y]

In [44]:
user_tag = user_tag.merge(genome_tags, on='tag', how='inner')

In [45]:
user_tag

userId         timestamp_x  movieId        tag         timestamp_y  \
0         65 2011-05-10 06:23:31      208  dark hero 2013-05-10 01:41:18   
1         65 2011-05-10 06:23:31      353  dark hero 2013-05-10 01:41:19   
2         65 2011-05-10 06:23:31      592  dark hero 2013-05-10 01:41:18   
3         65 2011-05-10 06:23:31     6874  dark hero 2013-05-10 01:41:19   
4        558 2010-12-20 01:00:53     5146  dark hero 2013-05-08 05:43:31   
...      ...                 ...      ...        ...                 ...   
6821  135425 2009-01-15 15:42:40     5349     comics 2013-05-16 17:53:54   
6822  135425 2009-01-15 15:42:40     8636     comics 2013-05-16 17:53:54   
6823  135425 2009-01-15 15:42:40    33794     comics 2013-05-16 17:53:54   
6824  136037 2015-03-26 11:45:38     6016     brazil 2015-03-26 11:45:58   
6825  136571 2015-01-30 03:04:50   126815    italian 2015-01-30 03:08:59   

      tagId  
0       288  
1       288  
2       288  
3       288  
4       288  
...     ...  
6821    234  
6822    234  
6823    234  
6824    161  
6825    571  

[6826 rows x 6 columns]

In [46]:
user_tag_cnt =  user_tag.groupby(['userId', 'tagId'], as_index=False)\
.agg({'tag':'count'}).rename({'tag':'tag_cnt'}, axis=1)

In [47]:
user_tag_sum = user_tag_cnt.groupby('userId', as_index=False).agg({'tag_cnt':'sum'})\
.rename({'tag_cnt':'user_tag_cnt_sum'}, axis=1)

In [48]:
user_tag_cnt = user_tag_cnt.merge(user_tag_sum, how='inner', on='userId')

In [49]:
user_tag_cnt['tag_cnt_mean'] = user_tag_cnt.tag_cnt / user_tag_cnt.user_tag_cnt_sum

In [50]:
user_tag = user_tag_cnt.pivot_table(index=['userId'], columns=['tagId'], values='tag_cnt_mean')
user_tag.fillna(0, inplace=True)

In [51]:
user_features

userId    Action  Adventure  Animation  Children    Comedy     Crime  \
0            1  0.376068   0.299145   0.042735  0.051282  0.205128  0.162393   
1            2  0.384615   0.230769   0.025641  0.025641  0.205128  0.025641   
2            3  0.242647   0.227941   0.029412  0.044118  0.330882  0.132353   
3            4  0.476190   0.238095   0.047619  0.095238  0.476190  0.190476   
4            5  0.240000   0.280000   0.100000  0.140000  0.380000  0.120000   
...        ...       ...        ...        ...       ...       ...       ...   
138488  138489  0.241379   0.206897   0.000000  0.034483  0.241379  0.241379   
138489  138490  0.022989   0.034483   0.000000  0.022989  0.183908  0.183908   
138490  138491  0.176471   0.352941   0.176471  0.235294  0.470588  0.000000   
138491  138492  0.250000   0.266667   0.050000  0.033333  0.583333  0.183333   
138492  138493  0.264228   0.280488   0.170732  0.199187  0.410569  0.113821   

        Documentary     Drama   Fantasy  ...    Horror      IMAX   Musical  \
0          0.000000  0.324786  0.179487  ...  0.299145  0.017094  0.008547   
1          0.000000  0.384615  0.025641  ...  0.205128  0.025641  0.025641   
2          0.000000  0.404412  0.132353  ...  0.147059  0.000000  0.036765   
3          0.000000  0.238095  0.095238  ...  0.000000  0.000000  0.047619   
4          0.000000  0.460000  0.140000  ...  0.020000  0.060000  0.100000   
...             ...       ...       ...  ...       ...       ...       ...   
138488     0.000000  0.517241  0.172414  ...  0.034483  0.034483  0.000000   
138489     0.000000  0.954023  0.022989  ...  0.011494  0.000000  0.034483   
138490     0.000000  0.176471  0.117647  ...  0.235294  0.000000  0.058824   
138491     0.100000  0.300000  0.150000  ...  0.000000  0.000000  0.033333   
138492     0.004065  0.455285  0.178862  ...  0.081301  0.032520  0.105691   

         Mystery   Romance    Sci-Fi  Thriller       War   Western    rating  
0       0.145299  0.051282  0.213675  0.316239  0.059829  0.034188  3.739316  
1       0.102564  0.153846  0.282051  0.333333  0.102564  0.051282  4.102564  
2       0.058824  0.110294  0.330882  0.272059  0.044118  0.014706  4.279412  
3       0.095238  0.190476  0.190476  0.476190  0.047619  0.047619  3.523810  
4       0.040000  0.260000  0.140000  0.280000  0.020000  0.040000  4.160000  
...          ...       ...       ...       ...       ...       ...       ...  
138488  0.137931  0.137931  0.103448  0.275862  0.000000  0.034483  3.931034  
138489  0.126437  0.206897  0.034483  0.183908  0.034483  0.011494  3.643678  
138490  0.000000  0.058824  0.235294  0.176471  0.000000  0.000000  2.647059  
138491  0.033333  0.283333  0.083333  0.116667  0.016667  0.066667  4.183333  
138492  0.093496  0.211382  0.150407  0.252033  0.040650  0.016260  4.252033  

[138493 rows x 21 columns]

In [52]:
user_tag = user_tag.reset_index()

In [54]:
user_features = user_features.merge(user_tag, on='userId', how='left')
user_features.fillna(0, inplace=True)

In [170]:
user_features_cols = list(user_features.columns)
user_features_cols.remove('userId')

In [164]:
user_features = user_features[user_features_cols]

userId    Action  Adventure  Animation  Children    Comedy     Crime  \
0       1  0.376068   0.299145   0.042735  0.051282  0.205128  0.162393   
1       2  0.384615   0.230769   0.025641  0.025641  0.205128  0.025641   
2       3  0.242647   0.227941   0.029412  0.044118  0.330882  0.132353   
3       4  0.476190   0.238095   0.047619  0.095238  0.476190  0.190476   
4       5  0.240000   0.280000   0.100000  0.140000  0.380000  0.120000   

   Documentary     Drama   Fantasy  ...    Horror      IMAX   Musical  \
0          0.0  0.324786  0.179487  ...  0.299145  0.017094  0.008547   
1          0.0  0.384615  0.025641  ...  0.205128  0.025641  0.025641   
2          0.0  0.404412  0.132353  ...  0.147059  0.000000  0.036765   
3          0.0  0.238095  0.095238  ...  0.000000  0.000000  0.047619   
4          0.0  0.460000  0.140000  ...  0.020000  0.060000  0.100000   

    Mystery   Romance    Sci-Fi  Thriller       War   Western    rating  
0  0.145299  0.051282  0.213675  0.316239  0.059829  0.034188  3.739316  
1  0.102564  0.153846  0.282051  0.333333  0.102564  0.051282  4.102564  
2  0.058824  0.110294  0.330882  0.272059  0.044118  0.014706  4.279412  
3  0.095238  0.190476  0.190476  0.476190  0.047619  0.047619  3.523810  
4  0.040000  0.260000  0.140000  0.280000  0.020000  0.040000  4.160000  

[5 rows x 21 columns]

In [27]:
# movie_features_cols = list(movie_features.columns)
# movie_features_cols.remove('movieId')
# movie_features = movie_features[movie_features_cols]
movie2id = {movieId: i for i, movieId in enumerate(movie_features.movieId)}
id2movie = {i: movieId for i, movieId in enumerate(movie_features.movieId)}

In [28]:
from lightfm import LightFM

model = LightFM(no_components=30, loss='warp')

C:\Users\ASO\anaconda3\lib\site-packages\lightfm\_lightfm_fast.py:9: UserWarning: LightFM was compiled without OpenMP support. Only a single thread will be used.
  warnings.warn(


In [37]:
model.fit(user_item, 
          user_features=csr_matrix(user_features.values),
          item_features=csr_matrix(movie_features.values),
          epochs=20, verbose=True)

Epoch: 100%|████████████████████████████████████████████████████████████████████████| 20/20 [1:43:06<00:00, 309.35s/it]


In [38]:
from lightfm.evaluation import precision_at_k
from lightfm.evaluation import auc_score

In [83]:
user_item_val = val.pivot_table(index=['userId'], columns=['movieId'], values='rating')
user_item_val = user_item_val.fillna(0)
user_item_val = csr_matrix(user_item_val.values)

In [74]:
train_precision = precision_at_k(model, user_item,
                                 user_features=csr_matrix(user_features),
                                 item_features=csr_matrix(movie_features),
                                 k=10).mean()

train_auc = auc_score(model, user_item,
                      user_features=csr_matrix(user_features),
                      item_features=csr_matrix(movie_features)).mean()


In [86]:
test_precision = precision_at_k(model, user_item_val, k=10,user_features=csr_matrix(user_features),
                      item_features=csr_matrix(movie_features)).mean()
test_auc = auc_score(model, user_item_val, user_features=csr_matrix(user_features),
                      item_features=csr_matrix(movie_features)).mean()

In [114]:
movie_ids = np.array([i for i in range(len(train.movieId.unique()))])

In [115]:
user_ids =np.array([0 for i in range(len(movie_ids))])

In [117]:
predictions = model.predict(user_ids, movie_ids, user_features=csr_matrix(user_features),
                      item_features=csr_matrix(movie_features), num_threads=4)

In [132]:
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import ndcg_score

In [149]:
val.sort_values(['userId','rating'], ascending=[True, False], inplace=True)

<ipython-input-149-bc4fc482f077>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  val.sort_values(['userId','rating'], ascending=[True, False], inplace=True)


In [ ]:
result_t = []
movie_ids = np.array([i for i in range(len(train.movieId.unique()))])

for user_id, user_seq in val.groupby('userId'):
    val_seq_len = user_seq.shape[0]
    true_scores = user_seq['movieId'].values.tolist()
    true_scores = np.asarray(true_scores[:10])
    n = min(10, len(true_scores))
    user_ids = np.array([user_id - 1 for i in range(len(movie_ids))])
    
    predictions = model.predict(user_ids, movie_ids, user_features=csr_matrix(user_features),
                      item_features=csr_matrix(movie_features), num_threads=4)
    
    predict_scores = np.argsort(predictions)[::-1][:n] #+ 1
    predict_scores = np.array([id2movie[k] for k in predict_scores])
    
    res = precision_recall_fscore_support(predict_scores, true_scores, average='weighted')
    precision, recall, f_score = res[0], res[1], res[2]
    
    predict_scores = np.array([predict_scores])
    true_scores = np.array([true_scores])
    ndcg_1 = ndcg_score(true_scores, predict_scores, k=1)
    ndcg_10 = ndcg_score(true_scores, predict_scores, k=10) 
    
    result_t.append([ndcg_1, ndcg_10])

In [157]:
train.sort_values(['userId','rating'], ascending=[True, False], inplace=True)

<ipython-input-157-504914969154>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train.sort_values(['userId','rating'], ascending=[True, False], inplace=True)


In [160]:
result_train = []
for user_id, userresult_train_seq in train.groupby('userId'):
    val_seq_len = user_seq.shape[0]
    true_scores = user_seq['movieId'].values.tolist()
    true_scores = np.asarray(true_scores[:10])
    n = min(10, len(true_scores))
    user_ids = np.array([user_id - 1 for i in range(len(movie_ids))])
    
    predictions = model.predict(user_ids, movie_ids, user_features=csr_matrix(user_features),
                      item_features=csr_matrix(movie_features), num_threads=4)
    
    predict_scores = np.argsort(predictions)[::-1][:n] + 1
    
    res = precision_recall_fscore_support(predict_scores, true_scores, average='weighted')
    precision, recall, f_score = res[0], res[1], res[2]
    
    predict_scores = np.array([predict_scores])
    true_scores = np.array([true_scores])
    ndcg_1 = ndcg_score(true_scores, predict_scores, k=1)
    ndcg_10 = ndcg_score(true_scores, predict_scores, k=10) 
    
    result_train.append([ndcg_1, ndcg_10])

C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classificat

C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classificat

C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classificat

C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classificat

C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classificat

...

C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classificat

C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1

C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classificat

C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\ASO\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1

MemoryError: Unable to allocate 18.7 MiB for an array with shape (2451270,) and data type float64

In [151]:
result = np.array(result)

In [161]:
result_train = np.array(result_train)

In [163]:
print('Precision: train %.2f, test %.2f.' % (train_precision, test_precision))
print('AUC: train %.2f, test %.2f.' % (train_auc, test_auc))
print('NDCG@1: train %.2f, test %.2f.' % (result_train.mean(axis=0)[0], result.mean(axis=0)[3]))
print('NDCG@10: train %.2f, test %.2f.' % (result_train.mean(axis=0)[1], result.mean(axis=0)[4]))

Precision: train 0.37, test 0.05.
AUC: train 0.82, test 0.75.
NDCG@1: train 0.46, test 0.48.
NDCG@10: train 0.72, test 0.78.
